<center>
<h1>NUMERICAL PYTHON</h1>
<br>

<h2> Python fo computational science </h2>
<h3> CINECA, 16-18 October 2017 </h3>

<h3> m.cestari@cineca.it </h3>

</center>

 <center>
 ![](files/images/rubber_duck.png)
 </center>

https://en.wikipedia.org/wiki/Rubber_duck_debugging

## Goal of the lecture

Learn 
* how to use the objects provided by numpy
* how to read data from files and manipulate it
* how to integrate python with plotting
* and of course ...


* ... how to have fun with it ...
<center>
![](files/images/xkcd.png)
</center>

In [1]:
import antigravity

but don't get overly exicted
<center>
![](files/images/coding_drunk.png)
</center>

## Introduction (1): history
* Numerical Python: evolution
 * In origin, 2 different libraries Numeric and Numarray
 * They became NumPy (2006). All the features of the two original libraries (plus more..) converging in one library


## Introduction (2): why bother?
* NumPy offers efficient array storing and computation
* Python scientific libraries (i.e. scipy, matplotlib, pandas) make use of NumPy objects
* NumPy is the __de facto__ standard

<center>
<h4>The Pydata stack</h4>
<img src="images/scientific-python-stack.jpg" width="650">
</center>

## Where are the bottlenecks?
Let’s start by trying to understand why high level languages like Python are slower than compiled code


In Python the main reasons of the "slowness" of the code are:

- Dynamic Typing
- Data (memory) Access 

## Dynamic typing
Even for simple operations, the Python interpreter has a fair bit of work to do. For example, in the statement `a+b`, the interpreter has to know which operation to invoke

 - If `a` and `b` are integers, then `a+b` requires sum of integers
 - If `a` and `b` are strings, then `a+b` requires string concatenation
 - If `a` and `b` are lists, then `a+b` requires list concatenation
 
The operator `+` is **overloaded**: its action depends on the type of the objects on which it acts

As a result, Python must check the type of the objects and then call the correct operation: **this involves substantial overheads**

## Static typing
Compiled languages avoid these overheads with explicit, static types; consider the following C code, which sums the integers from 1 to 10

```C
#include <stdio.h>

int main(void) {
    int i;
    int sum = 0;
    for (i = 1; i <= 10; i++) {
        sum = sum + i;
    }
    printf("sum = %d\n", sum);
    return 0;
}
```
The variables `i` and `sum` are explicitly declared to be integers, hence the meaning of addition here is completely unambiguous.

## Data Access

Another drag on speed for high level languages is data access; to illustrate, let’s consider the problem of summing some data, a collection of integers for example

### Summing with Compiled Code
In C or Fortran, these integers would typically be stored in an array, a simple data structure for storing homogeneous data. Such an array is stored in a single contiguous block of memory

For example, a 64 bit integer is stored in 8 bytes of memory and an array of `n` such integers occupies `8xn` consecutive memory slots. 

Moreover, the compiler is made aware of the data type by the programmer; in this case 64 bit integers,
hence each successive data point can be accessed by shifting forward in memory space by a known and fixed amount, in this case 8 bytes

## Data Access


### Summing in Pure Python

Python tries to replicate these ideas to some degree; for example, in the standard Python implementation (CPython), list elements are placed in memory locations that are in a sense contiguous

However, these list elements are more like pointers to data rather than actual data, hence there is still overhead involved in accessing the data values themselves

This is a considerable drag on speed: in fact it is generally true that the memory traffic is a major contributor to the "slowness" of the python code

Let’s look at some ways around these problems

## what's inside the box
<br>

<center>
<img src="images/numpy_pkgs.png" width="650">
</center>

## Using numpy

* Default for this presentation (and for the standard documentation)

In [2]:
import numpy as np

## numpy (main) objects

* NumPy provides two main objects:
 * __ndarray__;
 * __ufunc__;


## ndarray

Like lists, tuples and sets, ndarrays are collection of items
```python
>>> myarray, type(myarray)
(array([0, 1, 2, 3, 4, 5, 6, 7, 8]), numpy.ndarray)
```

## ndarray/2

Examples:

In [3]:
a = np.array([1., 2, 3])  # try also: 
                         # b = np.array([[1.5, 2.2, 34.4], [2.3, 4, 6.5]])
                         # c = np.array(['lof', 'l', 'ga']) 
a.dtype

dtype('float64')

In [4]:
c = np.array(['lof', 3, 2])  # doesn't work asexpected
c

array(['lof', '3', '2'],
      dtype='<U3')

## ndarray/3

* ndarray is a collection of __homogeneous__ items
 * Each item occupies the same number of bytes
* Items typically are numerical type...
* ... but an arbitrary __record__ of (non) numerical types can be used


## ndarray/4


`numpy/core/include/numpy/ndarrayobject.h`

<pre style="font-size:60%;"> 
typedef struct PyArrayObject {
char *data;     /* pointer to raw data buffer */ 
PyArray_Descr *descr; /* Pointer to type structure */ 
int nd;     /* number of dimensions, also called ndim */
npy_intp *dimensions;  /* size in each dimension (shape) */
npy_intp *strides;     /* bytes to jump to get to the next element in each dimension */
PyObject *base;   /* This object should be decref'd upon deletion of array */ 
                    /* For views it points to the original array */ 
int flags;             /* Flags describing array */
} PyArrayObject;
</pre>

## ndarray: data

```C
char *data;  /* pointer to raw data buffer */ 
PyArray_Descr *descr;/* pointer to type structure */
```

* `data` is just a pointer to bytes in memory
* `data` needs some sort of descriptor (dtype) to be interpreted


In [5]:
a = np.array([1, 2, 3])  # buffer of 12 bytes intepreted as 3 ints
a.dtype                  # int32 -> 32bits -> 4 bytes

dtype('int64')

In [6]:
b = a.astype(np.float)  # dtype('float64') 
b

array([ 1.,  2.,  3.])

## ndarray: some dtype types

<center>
<img src="images/dtypes.png" width="650">
</center>

## ndarray: dtype cont'ed

* the elements of `ndarrays` can be specified with a dtype object:


__numerical__
```python
>>> np.dtype(np.int32) # 32 are the bits used to 
dtype('np.int32')      # represent the integer  
                       # (4 bytes int) 
```
__strings__
```python
>>> np.dtype('S3') # mind the capital case here
                   # 3 means 3 bytes 
```
__both__
```python
>>> np.dtype([('f1', np.uint), ('f2', 'S3')])
dtype([('f', '<u4'), ('f2', '|S3')])# list of tuples
```

## Enough theory...

* Let's get our (dirty) hands on this new toy
* During this course, most of the things we learn will be used to solve an exercise
* It's about ...


![](files/images/break_bad.png)

## Exercise
* Rotate a molecule along the axes that diagonalize the moment of inertia tensor
* step by step guided solution through this course

![](files/images/mol.png)

## Exercise 1: dtype
Try to construct a dtype object to represent an atom in a 3d space. It should contain:
 * a string ('S3') to represent the symbol (i.e. Na, Cl, H, O)
 * an integer (np.int) for the atomic weight (i.e. 11, 17, 1)
 * 3 floats 64 bits (np.float64) for the cartesian coordinates

* Help needed? Try (after having imported numpy):
```
>>> help(np.dtype) (python)
>>> np.dtype? (ipython)
```

## Exercise 1: dtype
* Solution

In [7]:
dt = np.dtype([('symb','S3'),
               ('PA',np.int), 
               ('x',np.float64),
               ('y',np.float64),
               ('z',np.float64)]) 
dt

dtype([('symb', 'S3'), ('PA', '<i8'), ('x', '<f8'), ('y', '<f8'), ('z', '<f8')])

## ndarray/5


`numpy/core/include/numpy/ndarrayobject.h`

<pre style="font-size:60%;">
typedef struct PyArrayObject {
char *data;            /* pointer to raw data buffer */ 
PyArray_Descr *descr;  /* Pointer to type structure */ 
int nd;                /* number of dimensions, also called ndim */
npy_intp *dimensions;  /* size in each dimension (shape) */
npy_intp *strides;     /* bytes to jump to get to the next element in each dimension */
PyObject *base;        /* This object should be decref'd upon deletion of array */ 
                       /* For views it points to the original array */ 
int flags;             /* Flags describing array */
} PyArrayObject;
</pre>

## ndarray: dimensions

```C
int nd; /* number of dimensions, also called ndim */
 
npy_intp *dimensions;  /* size in each dimension */
``` 

In [8]:
b = np.array([ [1,2,5], [3,4,6] ])
b.shape

(2, 3)

In [9]:
b.shape

(2, 3)

In [10]:
b.shape = (6,1)  # reshaping the array
b

array([[1],
       [2],
       [5],
       [3],
       [4],
       [6]])

## numpy array summary

<img src="images/ndarray.png" alt="Drawing" style="width: 70%;"/>

## Creating arrays/1

__5 general mechanism__ to create arrays:

__(1)__ Conversion from other Python structures (e.g. lists, tuples): np.array function

In [11]:
list_ = [0,2,3,7]
a = np.array(list_)
print(a, type(a))

[0 2 3 7] <class 'numpy.ndarray'>


In [12]:
b = np.array([list_,list_])  # l, m python lists
b = np.asarray(b)    # convert b to an array if b is, 
                     # i.e. a list; otherwise does nothing 
b

array([[0, 2, 3, 7],
       [0, 2, 3, 7]])

## Creating arrays/2
 
__(2)__ Intrinsic `NumPy` array creation functions

In [13]:
a_ = np.zeros(10)
print(a_)
b_ = np.ones(shape=(3,2))
print(b_)
np.ones?

[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
[[ 1.  1.]
 [ 1.  1.]
 [ 1.  1.]]


In [14]:
c_ = np.linspace(0,10,70)  # start, stop, npoints 
print(c_)
print(c_.size)

[  0.           0.14492754   0.28985507   0.43478261   0.57971014
   0.72463768   0.86956522   1.01449275   1.15942029   1.30434783
   1.44927536   1.5942029    1.73913043   1.88405797   2.02898551
   2.17391304   2.31884058   2.46376812   2.60869565   2.75362319
   2.89855072   3.04347826   3.1884058    3.33333333   3.47826087
   3.62318841   3.76811594   3.91304348   4.05797101   4.20289855
   4.34782609   4.49275362   4.63768116   4.7826087    4.92753623
   5.07246377   5.2173913    5.36231884   5.50724638   5.65217391
   5.79710145   5.94202899   6.08695652   6.23188406   6.37681159
   6.52173913   6.66666667   6.8115942    6.95652174   7.10144928
   7.24637681   7.39130435   7.53623188   7.68115942   7.82608696
   7.97101449   8.11594203   8.26086957   8.4057971    8.55072464
   8.69565217   8.84057971   8.98550725   9.13043478   9.27536232
   9.42028986   9.56521739   9.71014493   9.85507246  10.        ]
70


In [15]:
d_ = np.arange(1,10,2)  # try also np.arange(1,10,2.)
print(d_) 

[1 3 5 7 9]


## Creating arrays/3
 
Try the shortcut: __np.r_ __



In [16]:
a = np.r_[0,1,2]  # ~ np.array
print(a)
a = np.r_[0:1:0.1]  # np.arange
print(a)
a = np.r_[0:2:20j]  # np.linspace
print(a)

[0 1 2]
[ 0.   0.1  0.2  0.3  0.4  0.5  0.6  0.7  0.8  0.9]
[ 0.          0.10526316  0.21052632  0.31578947  0.42105263  0.52631579
  0.63157895  0.73684211  0.84210526  0.94736842  1.05263158  1.15789474
  1.26315789  1.36842105  1.47368421  1.57894737  1.68421053  1.78947368
  1.89473684  2.        ]


## Creating arrays/4

__(4)__ Reading arrays from disk, either from standard or custom formats (mind the __byte order!!__)

```
loadtxt, genfromtxt  # custom ASCII formats

fromfile()           # custom binary
<ndarray>.tofile()      

h5py, pytables    # binary standard formats 
netcdf-python 
```

 ## Creating arrays/5

__Reading__ from ASCII text files
```
loadtxt(fname[, dtype=, comments=, ...])
```
__Save__ an array to ASCII text file (auto recognizes if .gz)  
```
savetxt(fname, X[, fmt=, delimiter=])
```

* `loadtxt` &emsp; is faster but less flexible
* `genfromtxt` &emsp; runs two loops, the first reads all the lines (→strings), the second parses the line and converts each string to a data type
 * It has the advantage of taking into account missing data


## Exercise 2: creating array

1. Create a ndarray of 6x5 elements, all set to 1
```
>>> help(np.ones)
```

2. Reshape the array to 3x10

3. Download 'mol.xyz' from here and build a new array of atom dtype
```
>>> help(np.loadtxt)
```

## Exercise 2: creating array

1.
```python
>>> a = np.ones((6,5))
```
2.
```python
>>> a.shape = 3,10
```
3.
```python
>>> dt = np.dtype([('symb','|S3'),('PA',np.int), ('x',np.float64),('y',np.float64),('z',np.float64)]) 
>>> arr = np.loadtxt('mol.xyz',dtype=dt)
```

In [17]:
dt = np.dtype([('symb','|S3'),('PA',np.int), ('x',np.float64),('y',np.float64), ('z', np.float64)])
arr = np.loadtxt('mol.xyz', dtype=dt)
print(arr)

[(b'C', 12,  -0.102, -0.301,  -0.276) (b'C', 12,  -0.024, -0.189,   1.125)
 (b'C', 12,   1.254, -0.165,   1.713) (b'C', 12,   2.406, -0.245,   0.941)
 (b'C', 12,   2.311, -0.359,  -0.456) (b'C', 12,   1.042, -0.388,  -1.058)
 (b'C', 12,  -1.248, -0.099,   1.954) (b'C', 12,  -1.288,  0.693,   3.11 )
 (b'C', 12,  -2.434,  0.786,   3.899) (b'C', 12,  -3.583,  0.07 ,   3.539)
 (b'C', 12,  -3.563, -0.728,   2.385) (b'C', 12,  -2.417, -0.807,   1.61 )
 (b'O', 16,  -4.755,  0.081,   4.233) (b'C', 12,  -4.849,  0.871,   5.418)
 (b'C', 12,  -6.253,  0.694,   5.978) (b'C', 12,  -6.478,  1.501,   7.263)
 (b'C', 12,  -7.892,  1.324,   7.828) (b'C', 12,  -8.114,  2.125,   9.104)
 (b'O', 16,  -9.453,  1.885,   9.535) (b'C', 12,  -9.9  ,  2.496,  10.668)
 (b'C', 12, -11.226,  2.214,  11.032) (b'C', 12, -11.774,  2.784,  12.17 )
 (b'C', 12, -11.027,  3.656,  12.986) (b'C', 12,  -9.706,  3.927,  12.605)
 (b'C', 12,  -9.138,  3.36 ,  11.464) (b'C', 12, -11.617,  4.262,  14.203)
 (b'C', 12, -12.527,  3.5

## Creating arrays/6
* From the ndarray just built we can save a binary file with the ndarray data

* It can be read with np.fromfile

* Be careful when using np.fromfile w/ fortran binary files, you may need to deal with __field separators__...


In [19]:
arr.tofile('mol_bin') 
arr2 = np.fromfile('mol_bin', dtype=dt) 
print(arr2)

[(b'C', 12,  -0.102, -0.301,  -0.276) (b'C', 12,  -0.024, -0.189,   1.125)
 (b'C', 12,   1.254, -0.165,   1.713) (b'C', 12,   2.406, -0.245,   0.941)
 (b'C', 12,   2.311, -0.359,  -0.456) (b'C', 12,   1.042, -0.388,  -1.058)
 (b'C', 12,  -1.248, -0.099,   1.954) (b'C', 12,  -1.288,  0.693,   3.11 )
 (b'C', 12,  -2.434,  0.786,   3.899) (b'C', 12,  -3.583,  0.07 ,   3.539)
 (b'C', 12,  -3.563, -0.728,   2.385) (b'C', 12,  -2.417, -0.807,   1.61 )
 (b'O', 16,  -4.755,  0.081,   4.233) (b'C', 12,  -4.849,  0.871,   5.418)
 (b'C', 12,  -6.253,  0.694,   5.978) (b'C', 12,  -6.478,  1.501,   7.263)
 (b'C', 12,  -7.892,  1.324,   7.828) (b'C', 12,  -8.114,  2.125,   9.104)
 (b'O', 16,  -9.453,  1.885,   9.535) (b'C', 12,  -9.9  ,  2.496,  10.668)
 (b'C', 12, -11.226,  2.214,  11.032) (b'C', 12, -11.774,  2.784,  12.17 )
 (b'C', 12, -11.027,  3.656,  12.986) (b'C', 12,  -9.706,  3.927,  12.605)
 (b'C', 12,  -9.138,  3.36 ,  11.464) (b'C', 12, -11.617,  4.262,  14.203)
 (b'C', 12, -12.527,  3.5

In [20]:
%%bash
ls -lrt mol_bin 

-rw-r--r-- 1 mirko mirko 2135 ott 15 10:53 mol_bin


## Creating arrays/7

__(5)__ Special library functions (e.g. random, ...) or _ad hoc_ defined function

In [21]:
def func(i, j):
    return i*j+1

np.fromfunction(func, (3,4))   # meshgrid

array([[ 1.,  1.,  1.,  1.],
       [ 1.,  2.,  3.,  4.],
       [ 1.,  3.,  5.,  7.]])

In [23]:
np.random.rand(4)

array([ 0.91556047,  0.13240769,  0.27650742,  0.79593441])

## Why a numpy array is useful?

memory-efficient container that provides fast numerical operations.


In [29]:
L = list(range(10000))

t1 = %timeit -o [i**2 for i in L]  # list elements squared

4.56 ms ± 234 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [30]:
a = np.arange(10000)

t2 = %timeit -n 1000 -o a**2

10.1 µs ± 3.12 µs per loop (mean ± std. dev. of 7 runs, 1000 loops each)


In [31]:
print("numpy speedUP:", t1.best/t2.best)

numpy speedUP: 698.4395632553798


## ndarray attributes

Some useful ndarray attributes are: (let arr be the array)
* __`arr.dtype`__ &emsp; data-type object for this array
```python
a = np.ones(10); a.dtype
dtype('float64')
```
* __`arr.shape`__ &emsp; returns a tuple with the size of the array. Changing the tuple re-shapes the array
* __`arr.ndim`__ &emsp; number of dimension in array
* __`arr.size`__ &emsp; total number of elements


## (some) ndarray functions
Some useful ndarray functions are:
* __`arr.copy()`__ &emsp; returns a copy of the array
* __`arr.view()`__ &emsp; returns a new view of the array using the same data of arr (save memory space)
* __`arr.reshape()`__ &emsp; returns an array with a new shape
* __`arr.transpose()`__ &emsp; returns an array view with the shape transposed


## (some) ndarray functions/2
* __`arr.sum()`__


In [ ]:
a = np.array([[1,4,2],[3,1,8]])
print(a)
print(a.shape)
a.sum(axis=1)  # try also axis=None

## (some) ndarray functions/3
```
>>> a = np.array([[1,1],[2,2]])
>>> a.sum(axis=0)
>>> array([ 3, 3])
```
![](files/images/sum.png)

## (some) ndarray functions/4
* __`arr.min|max()`__ &emsp; return min (or max) value
* __`arr.argmin|argmax()`__ &emsp; return the index of min (max) value
* __`arr.var|mean|std|prod()`__ &emsp; take the usual meaning


## (some) ndarray functions/5
__`sort`__ &emsp; array sorting
```python
>>> a = np.array([[1,4],[3,1]])
>>> np.sort(a)  # sort along the last axis
array([[1, 4],
       [1, 3]])
>>> np.sort(a, axis=0)  # sort along x axis
array([[1, 1],
       [3, 4]])
>>> np.sort(a, axis=None) # sort the flat array
array([1, 1, 3, 4])
>>> np.sort(a, order=field)  # 'field' of a structured array 
```

## Basic routines overview
* Creating arrays routines (mentioned earlier in this presentation)
* Operation on two or more arrays (`dot, ...`)
* Shape functions (`split, resize, concatenate, stack`)
* Basic functions (`average, cov, vectorize,...`)
* Two-dimensional array functions (`eye, diag, ...`)  


## Indexing
* Indexing means selecting some of the array's values
* ndarrays can be indexed using the following syntax:
<center>`X[obj]`</center>

<center>`X[obj]`</center>
Depending on __obj__, a different indexing is triggered:
* __Basic slicing__ when __obj__ is an integer, or a tuple (or list) ofintegers, and slice objects.
   * always returns a __view__ of the array
* __Record access__ when __obj__ is the string of a field of structured array
* __Advanced selection__ when __obj__ contains a ndarray of data type integer or bool.
   * always returns a copy of the array

## Basic slicing/1
* A slice object is represented by X[__<span style="color:blue">I</span>:<span style="color:green">J</span>:<span style="color:red">K</span>__]
 * __I__ = __<span style="color:blue">first element</span>__ (included, default is 0)
 * __J__ = __<span style="color:green">last element</span>__ (excluded, default is length of the array)
 * __K__ = __<span style="color:red">step or stride </span>__ (default is 1)
 
* Slicing for ndarray works similarly to standard Python sequences but can be done over __multiple dimensions__


## Basic slicing/2
Examples: given a two dimensional __5x10__ ndarray “A”
* `A[3] = A[3,:] = A[3,::]` &emsp; represents the __4th__ row of the array (10 elements)
* `A[:,1] = A[::,1]` &emsp; represents the __2nd__ column of the array (5 elements)


## Basic slicing/3

![](files/images/slice.png)

## Basic slicing/4
* Ellipses (...) can be used to replace zero or more “:” terms so that the total number of dimensions in the slicing tuple matches the shape of the ndarray

In [ ]:
a = np.arange(60) 
a.shape=(3,4,5) 
print(a[...,3])  # print a[:,:,3] → (3,4)
print('='*30)
print(a[1,...,3])  # print a[1,:,3] → (4)

## Exercise 3: Basic slicing
* Build a 2-dim array, then calculate all the average values along the rows for its odd and even columns.

![](files/images/slice_ex.png)

`hint: np.mean() or arr.mean()`

## Record access
The fields of structured arrays can be accessed by indexing the array with string
```python
>>> ra
array([(b'H', 1), (b'C', 6)], 
      dtype=[('at', 'S3'), ('Z', '<i4')])
>>> ra['at']   # array(['H', 'C'], dtype='|S3')
```

## Advanced selection
* Indexing arrays with other arrays
* `X[obj]` → `obj` is a `ndarray`
* There are two different ways:
 * __Boolean index arrays__. Involve giving a boolean array of the proper shape to indicate the values to be selected
 * __Integer index arrays__. Use one or more arrays of index values.


## Adv. selection: boolean index arrays
* ```python
  a = np.array([True, False, True])  # bool
  ```
* Boolean arrays must be of the (or _broadcastable_ to the) same shape of the array being indexed

In [ ]:
y = np.arange(18).reshape(3,6)
print(y)
y>6
b = y > 6
y[y>6]  # 1-d array

## Exercise 4 ndarray selection
* From the atoms array calculate the contribution to the molecular weight for each of the different kind of atoms (C, N, H, O) making use of the Numpy selection

$PM_c = \sum PA_c $

Hint: use the advanced boolean section

## Exercise 4 ndarray selection
* Solution
```python
>>> arr[arr['symb']=='C']['PA'].sum()  # 372
>>> arr[arr['symb']=='H']['PA'].sum()  # 26
>>> arr[arr['symb']=='N']['PA'].sum()  # 28
>>> arr[arr['symb']=='O']['PA'].sum()  # 32
```

## ndarray selection
To summarize, selection:
* can save you __time__ (and code lines)
* enhances the code __performances__
 * avoid traversing array through python loops 
 * internal (C) loops are still performed... more on that later)
* can save __memory__ (in place selection)
 


## NumPy (main) objects
NumPy provides two fundamental objects:
* __ndarray__;
* __ufunc__; functions that operate on one or more `ndarrays` __element-by-element__


## ufunc

## Universal functions/1
* Universal functions, ufuncs are functions that __operate__ on the `ndarray` objects 
* all `ufuncs` are instances of a general class, thus they behave the same. All `ufuncs` perform __element-by-element__ operations on the entire `ndarray(s)`
* These functions are __wrapper__ of some core functions, typically implemented in compiled (C or Fortran) code

## Universal functions/2

![](files/images/ufunc.png)

## Universal functions/3
* Ufunc loop may look something like
<pre style="font-size:50%;">
void ufunc_loop(void **args, int *dimensions, int *steps, void *data)
{
    /* int8 output = elementwise_function(int8 input_1, int8  
    * input_2)
    *
    * This function must compute the ufunc for many values at 
    * once, in the way shown below.
    */
    char *input_1 = (char*)args[0];
    char *input_2 = (char*)args[1];
    char *output = (char*)args[2];
    int i;
    for (i = 0; i < dimensions[0]; ++i) {
        *output = elementwise_function(*input_1, *input_2);
        input_1 += steps[0];
        input_2 += steps[1];
        output += steps[2];
    }
}
</pre>

## Universal functions/4

Examples:
```python
>>> a = np.array([a1,a2,...,an]) 
```
```python
>>> b = 1.5*a + 2   # * + / - all ufuncs 
```
* all the elements of “a” are multiplied by 1.5; result stored in a __temporary array__
* All the elements of the temp array are increased by 2; result stored in another __temporary array__
* b becomes a reference to the __second__ temp array


## Universal functions (3)
* What happens when ufunc has to operate on two arrays of __different dimensions__?
* To be efficient, element-wise operations are required
* To operate element-by-element broadcasting is needed.


![](files/images/broadcasting1.png)

![](files/images/broadcasting2.png)

## Broadcasting/1
* Broadcasting allows to deal in a meaningful way with inputs that do not have the same shape.
* After having applied the broadcasting rules the shape of all arrays must match
* let's see when different shapes are compatible from the broadcasting standpoint


## Broadcasting/2

Broadcasting follows these rules:

__1.__ Prepend 1 until all the arrays dimension matches

```
a.shape (2,2,3,6)  # a.ndim = 4  
b.shape (3,6)  # b.ndim = 2 

1 → b.ndim = 4
1 → b.shape (1,1,3,6)
```
 


__2.__  Arrays with a size of 1 along a particular dimension act like the array with the __largest size__ along that dimension.
 * The values of the array are assumed to be __the same along the broadcasted dimension__

## Broadcasting/3
* 1d-ndarrays are always broadcastable

```python
a.shape → (3)    b.shape -> (4,3);  
a.shape → (1,3)  # first rule, n. of dim matches
a.shape → (4,3)  # second rule
c = a*b 
c.shape → (4,3) # as expected  
```


```python
# another example
a.shape → (2,1,3)   
b.shape → (2,4,1);  
c = a*b c.shape → (2,4,3) # second rule

# Arrays not broadcastable
a.shape → (2,5,3)
b.shape → (2,4,1); 
c = a*b    # shape mismatch
```
 


## Broadcasting/4
* If needed it is possible to add a trailing dimension to the shape of a `ndarray`. This is a convenient way of taking the outer product (or any other outer operation) of two arrays
```python
a.shape → (3) b.shape → (4);  
c = a[:,np.newaxis]   # c.shape → (3,1)
c * b 
c.shape → (3,4)  
```

## Universal functions: performance
* Iterations over array should be avoided because they are not efficient. Performance using array arithmetics is better than using python loops.
 
* ~ 18x speedup (standard across NumPy)


In [ ]:
# Using ufunc
x = np.arange(10**7)
%timeit y = x*3

In [ ]:
# Using for loop
%timeit y = [x*3 for x in range(10**7)]    

## Efficiency note
The operation
```python
>>> b = 2*a + 2
```
can be done with in-place operations
```python
>>> b = a  # b is a reference to a
>>> b *= 2
>>> b += 2
```
More efficient and doesn't require storing temp array

These operations affect array “a” as well; we can avoid this with
```python
>>> b = a.copy()
```

Other in-place operations
```python
>>> b += a 
>>> b *= a 
>>> b **= a
>>> b -= a
>>> b /= a
```

## Efficiency note/2:
* Let's consider the function
```python
>>> def myfunc(x): #  if x is an array
        if x<0:  #  x<0 becomes a bool array
            return 0
        else:  
            return sin(x)
```

* “if x<0” results in a boolean array and __cannot__ be evaluated by the if statement

## Efficiency note (3): Vectorization
We can vectorize our function using the function where
```python
>>> def vecmyfunc(x):
        y = np.where(x<0, 0, np.sin(x))
        return y  # now returns an array
```
`np.where`
```python
np.where(condition, x, y)  # condition → bool array  
                           # condition is true → x  
                           # condition is false → y 
```

## NumPy universal functions/1
* There are more than 60 ufuncs
* Some `ufuncs` are called automatically: i.e. np.multiply(x,y) is called internally when a*b is typed
* NumPy offers trigonometric functions, their inverse counterparts, and hyperbolic versions as well as the exponential and logarithmic functions. Here, a few examples:

```python
>>> b = np.sin(a)
>>> b = np.arcsin(a)
>>> b = np.sinh(a)
>>> b = a**2.5   # exponential
>>> b = np.log(a)
>>> b = np.exp(a)
>>> b = np.sqrt(a)
```

## NumPy universal functions/2
* Comparison functions: __greater, less, equal, logical_and/_or/_xor/_nor, maximum, minimum, ...__
```python
>>> a = np.array([2,0,3,5])
>>> b = np.array([1,1,1,6])
>>> np.maximum(a,b)
array([2, 1, 3, 6])
```
* Floating point functions:  __floor, ceil, isreal, iscomplex,...__


## Exercise 5 
![](files/images/inertia_t.png)

## Exercise 5: universal functions
* Calculate the molecular center of mass
$$
xcm=\frac{1}{MW}\sum_ix_i m_i \;\;\;\;\;\;\;  
ycm=\frac{1}{MW}\sum_iy_i m_i \;\;\;\:\;\;\; 
zcm=\frac{1}{MW}\sum_iz_i m_i
$$  
  

Calculate the moment of inertia tensor
$$ 
\left[ \begin{array}{ccc}
I_{11} & I_{12} & I_{13} \\
I_{21} & I_{22} & I_{23} \\
I_{31} & I_{32} & I_{33} \end{array} \right] 
$$
whose elemets can be calculated as:
$$
I_{11} = I_{xx} = \sum_i m_i(y_i^2+z_i^2) \;\;\;\;\;\;\;
I_{11} = I_{xx} = \sum_i m_i(y_i^2+z_i^2) \;\;\;\;\;\;\;
I_{11} = I_{xx} = \sum_i m_i(y_i^2+z_i^2) 
$$
$$
I_{12} = I_{xy} = -\sum_i m_ix_iy_i \;\;\;\;\;\;\;
I_{12} = I_{xy} = -\sum_i m_ix_iz_i \;\;\;\;\;\;\;
I_{12} = I_{xy} = -\sum_i m_iy_iz_i
$$

In [ ]:
# molecular center of mass
MW = arr['PA'].sum() 
xcm = 1./MW * (arr['PA']*arr['x']).sum()
ycm = 1./MW * (arr['PA']*arr['y']).sum()
zcm = 1./MW * (arr['PA']*arr['z']).sum()
print(xcm,ycm,zcm)

In [ ]:
# moment of inertia tensor
Ixx = (arr['PA']*(arr['y']**2 + arr['z']**2)).sum()
Iyy = (arr['PA']*(arr['x']**2 + arr['z']**2)).sum()
Izz = (arr['PA']*(arr['x']**2 + arr['y']**2)).sum()
Ixy = -(arr['PA']*arr['x']*arr['y']).sum()
Ixz = -(arr['PA']*arr['x']*arr['z']).sum()
Iyz = -(arr['PA']*arr['y']*arr['z']).sum()

TI = np.array([[Ixx, Ixy, Ixz],[Ixy, Iyy, Iyz], [Ixz, Iyz, Izz]])
print(TI)
mTI = np.matrix(TI)

##  Standard classes inheriting from ndarray


## Matrix objects/1
`Matrix` objects inherit from ndarray classes
* Matrix can be created using a Matlab-style notation
```python
>>> a = np.matrix('1 2; 3 4')
>>> print a
[[1 2]
 [3 4]]
```

* Matrix are always __two-dimensional__ objects
* Matrix objects over-ride multiplication to be __matrix-multiplication__, and over-ride power to be __matrix raised to a power__
* Matrix objects have higher __priority__ than ndarrays. Mixed operations result therefore in a matrix object  

## Matrix objects/2

* Matrix objects have special attributes:
 * `.T` &emsp; returns the transpose of the matrix
 * `.H` &emsp; returns the conjugate transpose of the matrix
 * `.I` &emsp; returns the inverse of the matrix
 * `.A` &emsp; returns a view of the data of the matrix as a 2-d array 


## Basic modules

## Basic modules: linear algebra/1

Contains functions to solve __linear systems__, finding the __inverse__, the __determinant__ of a matrix, and computing __eigenvalues__ and __eigenvectors__


In [ ]:
# example

A = np.zeros((10,10)) # arrays initialization
x = np.arange(10)/2.0
for i in range(10):
    for j in range(10):
        A[i,j] = 2.0 + float(i+1)/float(j+i+1)
b = np.dot(A, x)
y = np.linalg.solve(A, b)  # A*y=b → y=x 
print(x)
print(y)
np.allclose(y,x, 10**-3)  # True, mind the tolerance!  

## Basic modules: linear algebra/2
* Eigenvalues can also be computed:

```python
# eigenvalues only:
>>> A_eigenvalues = np.linalg.eigvals(A)

# eigenvalues and eigenvectors:
>>> A_eigenvalues, A_eigenvectors = np.linalg.eig(A)
```

## Exercise 6: matrices and linalg

1.  From the array TI of the last exercise build a matrix (__mTI__), calculate eigenvalues (__e__) and eigenvectors (__Ev__) and prove that: 
$
Ev^T mTI \; Ev = 
\left[ \begin{array}{ccc}
e_1 & 0 & 0 \\
0 & e_2 & 0 \\
0 & 0 & e_3 \end{array} \right] 
$

2. Now, for example, you can rotate all the atoms coordinates by multiplying them by the __Ev__ matrix

In [ ]:
mTI = np.matrix(TI)
ev, Ev = np.linalg.eig(mTI)
print(ev)
Ev.T * mTI * Ev

## Basic modules: random numbers
* Calling the standard random module of Python in a loop to generate a sequence of random number is inefficient. Instead:

```python
>>> np.random.seed(100)
>>> x = np.random.random(4)
array([ 0.89132195, 0.20920212, 0.18532822,  
0.10837689])
>>> y = np.random.uniform(-1, 1, n)  # n uniform numbers in interval (-1,1)
``` 

* This module provides more general distributions like the normal distribution

```python
>>> mean = 0.0; stdev = 1.0
>>> u = np.random.normal(mean, stdev, n)
```

##  Exercise 7: random numbers
* Given a game in which you win back 10 times your bet if the sum of 4 dice is less than 10, determine (brute force, i.e. 1000000 trows) whether it is convenient to play the game or not

* hint: use `np.random.randint`

## Numpy: good to know

## Masked arrays (1)

```python
>>> x = np.arange(20).reshape(4,5)  # 2d array 
>>> x[2:,2:] = 2   # assignment
array([[ 0, 1, 2, 3, 4],
      [ 5, 6, 7, 8, 9],
      [10, 11, 2, 2, 2],
      [15, 16, 2, 2, 2]])
>>> x[x<5]  # x<5 bool array  
array([0, 1, 2, 3, 2, 2, 2, 2, 2, 2])  # 1d array
```

* What if we want to maintain the original shape of the array
* We can use masked arrays: the __shape of the array is kept__
* Invalid data can be flagged and ignored in math computations


In [ ]:
x = np.arange(20).reshape(4,5)
x[2:,2:] = 2
import numpy.ma as ma
y = ma.masked_greater(x, 4)
y

## Meshgrids/1
* Given a two-dimensional grid of points, namely $a_{i,j}=(x i , y j)$ we want to calculate for each point of the grid the values of a function $f(a_{ij})=f(x_i,y_j)$

* Suppose $f = \frac{x}{2} + y$

* $f\;$ is a `ufunc` (implicitly uses ufuncs: `add`, `divide`) so it operates element-by-element)

![](files/images/mesh.png)

In [ ]:
# wrong
def f(x,y): 
    return x/2 + y

x = np.linspace(0,4,5)
y = x.copy()

values = f(x,y)
values

## Meshgrids/2


In [ ]:
x = np.linspace(0,4,5)
y = x.copy()
xv,yv = np.meshgrid(x,y)
print(xv)
print(yv)

![](files/images/mesh2.png)

In [ ]:
values=f(xv,yv)
values

## Bibliography
* http://docs.scipy.org/doc/
* Guide to NumPy (Travis E. Oliphant)
* NumPy User Guide
* Numpy Reference Guide
* Python Scripting for Computational Science (HansPetter Langtangen)
